# Setting Everything up to get started

In [ ]:
import tensorflow as tf
import tensorflow_datasets as tfd
import matplotlib.pyplot as plt
import numpy as np

In [ ]:
def visualize_images(data):
    num_images = 5
    im = np.zeros((num_images * 28, num_images*28))
    k = 0
    for i in range(num_images):
        for j in range(num_images):
            im[i*28:(i+1)*28, j*28:(j+1)*28] = data[k]
            k += 1
    plt.imshow(im, cmap='gray')
    plt.show

## MLP

In [ ]:
mnist = tf.keras.datasets.mnist

(x_train, y_train), (x_test, y_test) = mnist.load_data()
visualize_images(x_train)

Creating a Data set

In [ ]:
training_data = tf.data.Dataset.from_tensor_slices((x_train,y_train.reshape(-1,))).shuffle(10000).batch(32)
test_data = tf.data.Dataset.from_tensors((x_test, y_test))

## Building the first simple model

In [ ]:
linear_model = tf.keras.models.Sequential([
    tf.keras.Input([28, 28]),
    tf.keras.layers.Flatten(),
    tf.keras.layers.Dense(10, activation=tf.nn.softmax)
])

opt = tf.keras.optimizers.SGD(learning_rate=0.001)
loss_fn = tf.keras.losses.SparseCategoricalCrossentropy()


@tf.function
def training_step(batch, labels):
    
    with tf.GradientTape() as tape:
        output=linear_model(batch)
        loss = loss_fn(labels, output)
        
    gradients = tape.gradient(loss, linear_model.trainable_weights)
    opt.apply_gradients(zip(gradients, linear_model.trainable_weights))
    
    return loss

In [ ]:
for _ in range(4):
    for i,(images, labels) in enumerate(training_data): 
        loss = training_step(images, labels)

        if not i % 500:
            print(i, " : ", loss.numpy())
    

## Evaluate Model

In [ ]:
def calculate_accuracy(model, dataset):
    correct_predictions = 0
    predictions = 0
    for images, labels in dataset:
        output = model(images)
        predictions += output.shape[0]
        correct_predictions += tf.reduce_sum(tf.cast(tf.equal(labels, tf.cast(tf.argmax(output, axis=-1), dtype=tf.uint8)), dtype=tf.float32))
    return correct_predictions / predictions

In [ ]:
print(calculate_accuracy(linear_model, training_data))
print(calculate_accuracy(linear_model, test_data))

Pretty good but not good enough

# First practice task let them create some fully connected layers

In [ ]:
MLP = tf.keras.models.Sequential([
    tf.keras.Input([28, 28]),
    tf.keras.layers.Flatten(),
    tf.keras.layers.Dense(100, activation=tf.nn.relu),
    tf.keras.layers.Dense(10, activation=tf.nn.softmax)
])

opt = tf.keras.optimizers.SGD(learning_rate=0.001)
loss_fn = tf.keras.losses.SparseCategoricalCrossentropy()


@tf.function
def training_step(batch, labels):
    
    with tf.GradientTape() as tape:
        output=MLP(batch)
        loss = loss_fn(labels, output)
        
    gradients = tape.gradient(loss, MLP.trainable_weights)
    opt.apply_gradients(zip(gradients, MLP.trainable_weights))
    
    return loss


for _ in range(4):
    for i,(images, labels) in enumerate(training_data): 
        loss = training_step(images, labels)

        if not i % 500:
            print(i, " : ", loss.numpy())
            
print(calculate_accuracy(MLP, training_data).numpy())
print(calculate_accuracy(MLP, test_data).numpy())


# Going to fashion

In [ ]:
mnist = tf.keras.datasets.fashion_mnist

(x_train, y_train), (x_test, y_test) = mnist.load_data()
x_train = tf.cast(x_train, tf.float32)
x_test = tf.cast(x_test, tf.float32)
visualize_images(x_train)

training_data = tf.data.Dataset.from_tensor_slices((x_train,y_train.reshape(-1,))).shuffle(10000).batch(32)
test_data = tf.data.Dataset.from_tensors((x_test, y_test))

In [ ]:
for _ in range(4):
    for i,(images, labels) in enumerate(training_data): 
        loss = training_step(images, labels)

        if not i % 500:
            print(i, " : ", loss.numpy())
    

In [ ]:
print(calculate_accuracy(MLP, training_data).numpy())
print(calculate_accuracy(MLP, test_data).numpy())

ooooh

# CNN time

In [ ]:
cnn = tf.keras.models.Sequential([
    tf.keras.Input([28, 28]),
    tf.keras.layers.Reshape([28,28,1]),
    tf.keras.layers.Conv2D(8, kernel_size=3,padding='valid', activation=tf.nn.relu),
    tf.keras.layers.Conv2D(16, kernel_size=3,padding='valid', activation=tf.nn.relu),
    tf.keras.layers.Flatten(),
    tf.keras.layers.Dense(10, activation=tf.nn.softmax)
])

@tf.function
def training_step(batch, labels):
    
    with tf.GradientTape() as tape:
        output=cnn(batch)
        loss = loss_fn(labels, output)
        
    gradients = tape.gradient(loss, cnn.trainable_weights)
    opt.apply_gradients(zip(gradients, cnn.trainable_weights))
    
    return loss

In [ ]:
for _ in range(4):
    for i,(images, labels) in enumerate(training_data): 
        loss = training_step(tf.cast(images,tf.float32), labels)

        if not i % 500:
            print(i, " : ", loss.numpy())

In [ ]:
print(calculate_accuracy(cnn, training_data).numpy())
print(calculate_accuracy(cnn, test_data).numpy())

In [ ]:
cnn = tf.keras.models.Sequential([
    tf.keras.Input([28, 28]),
    tf.keras.layers.Reshape([28,28,1]),
    tf.keras.layers.Conv2D(64, kernel_size=3,padding='valid', activation=tf.nn.relu),
    tf.keras.layers.Conv2D(32, kernel_size=3,padding='valid', activation=tf.nn.relu),
    tf.keras.layers.Conv2D(16, kernel_size=3,padding='valid', activation=tf.nn.relu),
    tf.keras.layers.Conv2D(8, kernel_size=3,padding='valid', activation=tf.nn.relu),
    tf.keras.layers.Conv2D(4, kernel_size=3,padding='valid', activation=tf.nn.relu),
    tf.keras.layers.Flatten(),
    tf.keras.layers.Dense(10, activation=tf.nn.softmax)
])

@tf.function
def training_step(batch, labels):
    
    with tf.GradientTape() as tape:
        output=cnn(batch)
        loss = loss_fn(labels, output)
        
    gradients = tape.gradient(loss, cnn.trainable_weights)
    opt.apply_gradients(zip(gradients, cnn.trainable_weights))
    
    return loss

In [ ]:
for _ in range(4):
    for i,(images, labels) in enumerate(training_data): 
        loss = training_step(tf.cast(images,tf.float32), labels)

        if not i % 500:
            print(i, " : ", loss.numpy())

In [ ]:
print(calculate_accuracy(cnn, training_data).numpy())
print(calculate_accuracy(cnn, test_data).numpy())

# RNNs

In [ ]:
path_to_file = tf.keras.utils.get_file('shakespeare.txt', 'https://storage.googleapis.com/download.tensorflow.org/data/shakespeare.txt')
text = open(path_to_file, 'rb').read().decode(encoding='utf-8')
print ('Length of text: {} characters'.format(len(text)))
print(text[:250])



In [ ]:
characters = sorted(set(text))

In [ ]:
print(len(characters))

In [ ]:
char_to_index = {u:i for i, u in enumerate(characters)}
index_to_char = np.array(characters)
text_int = np.array([char_to_index[k] for k in text])

data = tf.data.Dataset.from_tensor_slices(text_int).batch(100, drop_remainder=True).shuffle(1000).repeat().batch(16, drop_remainder=True)

In [ ]:
for seq in data:
    #print(seq)
    #print([index_to_char[i] for i in seq.numpy()])
    break

In [ ]:

opt = tf.keras.optimizers.Adam(learning_rate=0.1)
rnn = tf.keras.models.Sequential([
    tf.keras.Input([100, 65]),
    tf.keras.layers.LSTM(30, 
                       return_sequences=True,),
    tf.keras.layers.Dense(65)
])
loss_fn = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)
for i, seq in enumerate(data):
    one_hot_seq = tf.one_hot(seq, depth=65, axis=-1)
    input_seq = one_hot_seq[:,:-1]
    output_seq = seq[:,1:]
    
    with tf.GradientTape() as tape:
        output = rnn(input_seq)
        loss = tf.reduce_mean(loss_fn(output_seq,output))
    
    gradients = tape.gradient(loss, rnn.trainable_weights)
    opt.apply_gradients(zip(gradients, rnn.trainable_weights))
    
    rnn.reset_states() 
    
    if not i % 100 :
        print(i, loss)
        
    if i >= 2000:
        break

## look at generation

In [ ]:
start_letter = 'l'
start_letter_index = np.array([char_to_index[start_letter]])
print(start_letter_index)

reshaped = tf.reshape(start_letter_index, [1,1])

print(reshaped)
next_input = tf.one_hot(reshaped, axis=-1, depth=65)

gen_text = str(start_letter)

rnn.reset_states()

for i in range(500):
    n = rnn(next_input)
    # tmp = np.asarray([np.argmax(n[0,0].numpy())])
    tmp = np.random.choice(65, 1, p=tf.nn.softmax(n[0,0]).numpy())
    gen_text += index_to_char[tmp[0]]
    next_input = tf.one_hot(tf.reshape(tmp, [1,1]), axis=-1, depth=65)

print(gen_text)